In [1]:
## Importing Qiskit libraries
from qiskit import QuantumRegister, ClassicalRegister, QuantumCircuit, transpile, AncillaRegister, Aer, execute, assemble
from qiskit_aer import AerSimulator
from qiskit.circuit import Gate
from qiskit.visualization import plot_histogram, circuit_drawer
import matplotlib.pyplot as plt
from qiskit.quantum_info import Operator
from qiskit.circuit.library import MCMT, RYGate, RXGate, PhaseGate
import numpy as np
np.set_printoptions(threshold=np.inf)
import math
from typing import Union
from numpy import linalg
from scipy.linalg import expm
import pickle
from numba import jit

In [21]:
## Settings
d = 1 # of dimensions
M = 1 # of registers (rough estimate for M is the number of particles in the final state, but M should be set so that p_success can be maximized)
n = 1 # of particles in the initial state
N_abs = 1 # of modes for momenta

nqubits = N_abs * d + d + 1
N_s = 2 ** (N_abs + 1) # size of the lattice per one dimension
V = N_s ** d # volume
N = N_abs * d + d + 1 # of qubits per one particle (magnitude of momentum + sign + occupation)
s = math.ceil(math.log2(math.factorial(M)/math.factorial(M - n))) # of ancilla qubits for Bose symm.

In [3]:
I = np.array([[1, 0], [0, 1]])
H = np.array([[1/np.sqrt(2), 1/np.sqrt(2)], [1/np.sqrt(2), -1/np.sqrt(2)]])
X = np.array([[0, 1], [1, 0]])
Y = np.array([[0, -1j], [1j, 0]])
Z = np.array([[1, 0], [0, -1]])

In [2]:
#初期状態|0000・・・0>を準備する。
def StateZeros(nqubits):
    State = np.zeros(2**nqubits)
    State[0]=1
    return State

In [3]:
def makeGate(N, nqubit, Gate): # action of Gate to n'th qubit (n = 0...N)
    if nqubit == 0:
        tmp = Gate
    else: tmp = I
    for i in range(N):
        B_tmp = np.zeros((2 ** (i + 2), 2 ** (i + 2)))
        if nqubit == i + 1:
            B_tmp = np.kron(Gate, tmp)
        else: B_tmp = np.kron(I, tmp)
        tmp = B_tmp
    return tmp

# example of use:
# makeGate(N, (N_abs + 1) * d, X)
# makeGate(1, 1, H)

In [100]:
def showNonZeroCol(mat):
    list = []
    for i in range(len(mat[0])):
        if mat[i][0] != 0:
            list.append(mat[i][0])
            print(i)
    print(list)

def showNonZeroAll(mat):
    mat_list = []
    raw_list = []
    column_list = []
    for i in range(len(mat[0])):
        for j in range(len(mat[0])):
            if mat[i][j] != 0:
                raw_list.append(i)
                column_list.append(j)
                mat_list.append(mat[i][j])
    print('raw list', raw_list)
    print('column list', column_list)
    print('mat', mat_list)

In [4]:
# def transPosition2Momentum(qmom, sign): # if sign is True, we have to transform qmom to qposition
#     if sign == 'position':
#         qmom = qmom - (N / 2)
#     return qmom

In [5]:
# if dagger is True, make an annihilation operator, if False, an creation operator
# ireg means the number of the register acted
# qmom means that the momentum with sign
def annihilationCreationOpPerReg(qmom, ireg, dagger, N, M):
    if qmom > 0:
        qrow = int(qmom - 1/2 + 2 ** (N-1) + 2 ** N_abs)
    elif qmom < 0:
        qrow = int(np.abs(qmom + 1/2) + 2 ** (N-1))
    tmp_op = np.zeros((2 ** N, 2 ** N))
    if dagger == False:
        tmp_op[0][qrow] = 1
    else:
        tmp_op[qrow][0] = 1
    identity = np.eye(2 ** N)
    if ireg == 0:
        tmp = tmp_op
    else: tmp = identity
    # print(tmp)
    for i in range(M-1):
        # print(i)
        B_tmp = np.zeros((2 ** (i + 2), 2 ** (i + 2)))
        if ireg == i + 1:
            B_tmp = np.kron(tmp_op, tmp)
        else:
            B_tmp = np.kron(identity, tmp)
        tmp = B_tmp
    return tmp

def annihilationCreationOpPerRegInPos(ipos, ireg, dagger, N, M):
    qrow = int(ipos + 2 ** (N-1))
    tmp_op = np.zeros((2 ** N, 2 ** N))
    if dagger == False:
        tmp_op[0][qrow] = 1
    else:
        tmp_op[qrow][0] = 1
    identity = np.eye(2 ** N)
    if ireg == 0:
        tmp = tmp_op
    else: tmp = identity
    # print(tmp)
    for i in range(M-1):
        # print(i)
        B_tmp = np.zeros((2 ** (i + 2), 2 ** (i + 2)))
        if ireg == i + 1:
            B_tmp = np.kron(tmp_op, tmp)
        else:
            B_tmp = np.kron(identity, tmp)
        tmp = B_tmp
    return tmp

def annihilationCreationOp(qmom, dagger, sign):
    tmp_op = np.zeros((2 ** (N * M), 2 ** (N * M)))
    # print(tmp_op.size)
    for ireg in range(M):
        # print(annahilationCreationOpPerReg(qmom, ireg, dagger, N, M).size)
        if sign == 'momentum':
            tmp_op += annihilationCreationOpPerReg(qmom, ireg, dagger, N, M)
        elif sign == 'position':
            tmp_op += annihilationCreationOpPerRegInPos(qmom, ireg, dagger, N, M)
        else: print('sign should be momentum or position!')
    return tmp_op * (1/np.sqrt(M))

# example of use
# N_abs = 2
# N = 4
# M = 1
# annahilationCreationOpPerRegInPos(2, 0, False, N, M)

In [6]:
# annihilationCreationOpPerRegInPos(ipos=3, ireg=0, )

In [7]:
# to ajustment the dimension of Hilbert space with QC algorithnm, we must add ancilla qubits
def addAncilla(mat, N_abs, n, d, s):
    free_num = (N_abs + math.log2(n)) * d
    bose_num = s + 1
    anc_eye_mat = np.eye(2 ** int(free_num + bose_num))
    return np.kron(anc_eye_mat, mat)

In [8]:
import cmath
# flip alignment code and QFT code
def changeBasis(N):
    tmp = np.eye(2 ** N)
    for i in range(2 ** (N - 2)):
        tmp[2 ** (N - 1) + i][2 ** (N - 1) + i] = 0
        tmp[2 ** (N - 1) + i][2 ** (N - 1) + 2 **(N - 2) - i - 1] = 1
    return tmp

def dft_matrix(num):
    A = np.arange(num)
    B = A.reshape(1, -1)
    C = A.reshape(-1, 1)
    M = cmath.e**(-1j * 2 * cmath.pi * B * C  / num)
    return M * (1/np.sqrt(num))

def qft(N):
    return np.kron(np.eye(2), dft_matrix(2 ** (N - 1)))

In [9]:
def makeGatePerReg(Gate, M): # make tensor M products of Gate 
    tmp = Gate
    for i in range(M - 1):
        B_tmp = np.zeros((2 ** (N * i), 2 ** (N * i)))
        B_tmp = np.kron(Gate, tmp)
        tmp = B_tmp
    return tmp

In [10]:
# annahilationCreationOpPerReg(3/2, 0, False, 3, 2, 'momentum')
# annahilationCreationOp(1, True)

In [11]:
def momentum2omega(qmom, m, a_s):
    N_s = 2 ** (N_abs + 1) # number of lattice per dimension
    pmom = ((2 * np.pi) / (N_s * a_s)) * qmom
    omega = np.sqrt(pmom ** 2 + m ** 2)
    return omega

In [12]:
def sqij(qmom, ireg, jreg, m, a_s):
    omega = momentum2omega(qmom, m, a_s)
    zq = (1/2) * np.log(omega)
    A = annihilationCreationOpPerReg(qmom, ireg, True, N, M)
    B = annihilationCreationOpPerReg(-qmom, jreg, True, N, M)
    C = annihilationCreationOpPerReg(-qmom, jreg, False, N, M)
    D = annihilationCreationOpPerReg(qmom, ireg, False, N, M)
    ln_sq = -((2 * zq)/M) * (A @ B - C @ D) # 2 means that q and -q are calulated simultaneously
    sq_ij = expm(ln_sq)
    return sq_ij

# squeezing operation for verifying QC algorithms
def sqDebug(m, a_s):
    sq = np.eye(2 ** (N * M), dtype='complex128')
    for qmom in range(2 ** (N_abs * d)-1, -1, -1):
        for ireg in range(M-1, -1, -1):
            for jreg in range(M-1, -1, -1):
                if ireg != jreg:
                    # print('qmom, ireg, jreg', qmom, ireg, jreg)
                    sq @= sqij(qmom + 1/2, ireg, jreg, m, a_s)
    return sq

def squeezeOpPerMom(qmom, m, a_s):
    omega = momentum2omega(qmom, m, a_s)
    zq = (1/2) * np.log(omega)
    A = annihilationCreationOp(qmom, True, 'momentum')
    # print('A is', A)
    B = annihilationCreationOp(-qmom, True, 'momentum')
    # print('B is', B)
    C = annihilationCreationOp(-qmom, False, 'momentum')
    # print('C is', C)
    D = annihilationCreationOp(qmom, False, 'momentum')
    # print(linalg.norm(A @ B, 2))
    ln_sq = -2 * zq * (A @ B - C @ D)
    sq = expm(ln_sq)
    return sq

def squeezeOpQProd(m, a_s): # corresponds to \prod exp{\sum_{i} a^{i} + a^{i}^{dagger}}
    sq = np.eye(2 ** (N * M))
    for q in range(2 ** (N_abs * d)-1, -1, -1):
        # print(q)
        # print(squeezeOpPerMom(q+1/2))
        # print(squeezeOpPerMom(-(q+1/2)))
        # print('qmom', q + 1/2)
        sq @= squeezeOpPerMom(q + 1/2, m, a_s)
        # sq @= squeezeOpPerMom(-(q + 1/2))
    return sq

def squeezingOp(m, a_s):
    ln_sq = np.zeros((2 ** (N * M), 2 ** (N * M)))
    for s in range(2):
        sign = (-1) ** s
        for q in range(2 ** (N_abs * d)-1, -1, -1):
            qmom = (q + 1/2) * sign
            # print('qmom', qmom)
            omega = momentum2omega(qmom, m, a_s)
            zq = (1/2) * np.log(omega)
            A = annihilationCreationOp(qmom, True, 'momentum')
            B = annihilationCreationOp(-qmom, True, 'momentum')
            C = annihilationCreationOp(-qmom, False, 'momentum')
            D = annihilationCreationOp(qmom, False, 'momentum')
            ln_sq += -zq * (A @ B - C @ D)
    return expm(ln_sq)

In [13]:
# ## Scheme of Squeezing operation
# M = 2
# N_abs = 1
# d = 1
# N = N_abs * d + d + 1
# n = 1
# s = math.ceil(math.log2(math.factorial(M)/math.factorial(M - n))) # of ancilla qubits for Bose symm.
# tau_0 = 0.5 # Wigner delay
# tau_I = 0 # length of time of interaction
# delta = 1 # time step
# m_0 = 0 # chosen to represent a relevant enrgy scale in the weak coupling regime
# tau = 0
# m_t = m_0
# lambda_t = 1
# a_s = 1

# m_ren = m_0
# lambda_ren = 1
# free_num = int((N_abs + math.log2(n)) * d)
# bose_num = int(s + 1)
# state = StateZeros(((N * M) + (free_num + bose_num)))
# count = 0
# mat = addAncilla(sqij(qmom=1/2, ireg=0, jreg=1, m=0, a_s=1), N_abs, n, d, s)

# m = 0
# a_s = 1
# # mat = addAncilla(sqDebug(m, a_s), N_abs, n, d, s)
# # state = np.dot(mat, state)

# list = []
# for i in range(len(mat[0])):
#     if mat[i][0] != 0:
#         list.append(mat[i][0])
#         print(i)
# list

In [107]:
M = 3
N_abs = 1
d = 1
N = N_abs * d + d + 1
n = 1
delta = 1
lam = 1
Delta = (delta * 100 * 12 * lam) / (96 * (M ** 2))

ipos = 0
ireg = 0
jreg = 0
kreg = 1
lreg = 2

A = annihilationCreationOpPerRegInPos(ipos, ireg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, ireg, True, N, M)
B = annihilationCreationOpPerRegInPos(ipos, jreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, jreg, True, N, M)
C = annihilationCreationOpPerRegInPos(ipos, kreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, kreg, True, N, M)
D = annihilationCreationOpPerRegInPos(ipos, lreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, lreg, True, N, M)
ln_tmp = -1j * Delta * (A @ B @ C @ D)
mat1 = expm(ln_tmp)
print('ipos', ipos)
showNonZeroAll(ln_tmp)
showNonZeroCol(mat1)
ipos = 3
A = annihilationCreationOpPerRegInPos(ipos, ireg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, ireg, True, N, M)
B = annihilationCreationOpPerRegInPos(ipos, jreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, jreg, True, N, M)
C = annihilationCreationOpPerRegInPos(ipos, kreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, kreg, True, N, M)
D = annihilationCreationOpPerRegInPos(ipos, lreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, lreg, True, N, M)
ln_tmp = -1j * Delta * (A @ B @ C @ D)
mat2 = expm(ln_tmp)
print('ipos', ipos)
showNonZeroAll(ln_tmp)
showNonZeroCol(mat2)

# showNonZero(mat1)

# showNonZero(mat2)

ipos 0
raw list [0, 4, 32, 36, 256, 260, 288, 292]
column list [288, 292, 256, 260, 32, 36, 0, 4]
mat [-1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j]
0
288
[(0.18090578132334068+0j), -0.9835004312575524j]
ipos 3
raw list [0, 7, 56, 63, 448, 455, 504, 511]
column list [504, 511, 448, 455, 56, 63, 0, 7]
mat [-1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j]
0
504
[(0.18090578132334068+0j), -0.9835004312575524j]


In [178]:
def intUnij(ireg, jreg, kreg, lreg, ipos, Delta):
    ln_exp = np.eye(2 ** (N * M), dtype='complex128')
    A = annihilationCreationOpPerRegInPos(ipos, ireg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, ireg, True, N, M)
    B = annihilationCreationOpPerRegInPos(ipos, jreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, jreg, True, N, M)
    C = annihilationCreationOpPerRegInPos(ipos, kreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, kreg, True, N, M)
    D = annihilationCreationOpPerRegInPos(ipos, lreg, False, N, M) + annihilationCreationOpPerRegInPos(ipos, lreg, True, N, M)
    ln_exp = -1j * Delta * (A @ B @ C @ D)
    # print('I am here')
    # showNonZeroAll(ln_exp)
    return expm(ln_exp)

# interaction Hamiltonian for verifying QC algorithms
def intUDebug(delta, lam):
    Delta = (delta * lam) / (96 * (M ** 2))
    int_u = np.eye(2 ** (N * M), dtype='complex128')
    for ipos in range(2 ** (N_abs * d + d)-1, -1, -1):
        for ireg in range(M):
            for jreg in range(M):
                for kreg in range(M):
                    for lreg in range(M):
                        int_u @= intUnij(ireg, jreg, kreg, lreg, ipos, Delta)
    return int_u

def phi(n):
    A = annihilationCreationOp(n, True, 'position')
    B = annihilationCreationOp(n, False, 'position')
    phiGate = (1/np.sqrt(2)) * (A + B)
    return phiGate

# exact value of interaction Hamiltonian time evolution
def intU(delta, lam):
    ln_UI = 0
    for ipos in range(2 ** (N_abs * d + d)):
        ln_UI += -1j * ((delta * lam) / 24) * (phi(ipos) @ phi(ipos) @ phi(ipos) @ phi(ipos))
        print(expm(-1j * ((delta * lam) / 24) * (phi(ipos) @ phi(ipos) @ phi(ipos) @ phi(ipos))))
    uI = expm(ln_UI)
    return uI

# approximation for commutation error in [a_m, a_n^dagger]
def intUNProd(delta, lam):
    uI = np.eye(2 ** (N * M), dtype='complex128')
    for ipos in range(2 ** (N_abs * d + d)):
        # print(expm(-1j * ((delta * lam) / 24) * (phi(ipos) @ phi(ipos) @ phi(ipos) @ phi(ipos))))
        uI @= expm(-1j * ((delta * lam) / 24) * (phi(ipos) @ phi(ipos) @ phi(ipos) @ phi(ipos)))
    return uI

In [175]:
# The same pattern with QC algorithms
def intUDebug2(delta, lam):
    Delta = (delta * lam) / (96 * (M ** 2))
    int_u = np.eye(2 ** (N * M), dtype='complex128')
    for ipos in range(2 ** (N_abs * d + d) -1, -1, -1):
        # print('ipos', ipos)
    #     dummy = 0
    # if dummy == 0:
    #     ipos = 0
        # all differ
        for ireg in range(M-1, -1, -1):
            for jreg in range(M-1, -1, -1):
                for kreg in range(M-1, -1, -1):
                    for lreg in range(M-1, -1, -1):
                        if ireg < jreg and jreg < kreg and kreg < lreg:
                            # print('all differ;', 'ireg', ireg, 'jreg', jreg, 'kreg', kreg, 'lreg', lreg)
                            int_u @= intUnij(ireg, jreg, kreg, lreg, ipos, 24 * Delta)

        # 2 indices match
        for ireg in range(M-1, -1, -1):
            for jreg in range(M-1, -1, -1):
                for kreg in range(M-1, -1, -1):
                    if ireg != jreg and ireg != kreg and jreg < kreg:
                        # print('2 indices;', 'ireg', ireg, 'jreg', jreg, 'kreg', kreg)
                        int_u @= intUnij(ireg, ireg, jreg, kreg, ipos, 12 * Delta)

        # 2 pairs of indices match
        for ireg in range(M-1, -1, -1):
            for jreg in range(M-1, -1, -1):
                if ireg < jreg:
                    # print('2 pairs match;', 'ireg', ireg, 'jreg', jreg)
                    int_u @= intUnij(ireg, ireg, jreg, jreg, ipos , 6 * Delta)

        # 3 indices match
        for ireg in range(M-1, -1, -1):
            for jreg in range(M-1, -1, -1):
                if ireg < jreg:
                    # print('3 indices;', 'ireg', ireg, 'jreg', jreg)
                    int_u @= intUnij(ireg, ireg, ireg, jreg, ipos, 8 * Delta)

        # 4 indices match
        for ireg in range(M-1, -1, -1):
            # print('4 indices match;', 'ireg', ireg)
            int_u @= intUnij(ireg, ireg, ireg, ireg, ipos, Delta)
            
    return int_u

In [260]:
M = 3
N_abs = 1
d = 1
N = N_abs * d + d + 1
n = 1
delta = 1
lam = 1
Delta = (delta * 100 * lam) / (96 * (M ** 2))
mat = intUnij(ireg=1, jreg=1, kreg=2, lreg=0, ipos=2, Delta=Delta)

showNonZeroCol(mat)

0
390


[(0.993309514238751+0j), -0.11548250483418028j]

今日判明したこと
two indices matchがpositionに対して対象でないことがわかった
このエラーは、発生する時としない時がある

In [173]:
M = 3
N_abs = 1
d = 1
N = N_abs * d + d + 1
n = 1
delta = 1
lam = 1
Delta_t = (delta * 100 * lam) / (96 * (M ** 2))
mat1 = np.eye(2 ** (N * M), dtype='complex128')
mat2 = np.eye(2 ** (N * M), dtype='complex128')
# mat @= intUnij(ireg=2, jreg=2, kreg=0, lreg=1, ipos=0, Delta=12 * Delta_t)
# mat @= intUnij(ireg=1, jreg=1, kreg=0, lreg=2, ipos=0, Delta=12 * Delta_t)
mat1 @= intUnij(ireg=0, jreg=0, kreg=1, lreg=2, ipos=0, Delta=12 * Delta_t)
print('mat1 first')
showNonZeroCol(mat1)
mat1 @= intUnij(ireg=1, jreg=1, kreg=1, lreg=2, ipos=0, Delta=8 * Delta_t)
print('mat1 second')
showNonZeroCol(mat1)
mat2 @= intUnij(ireg=0, jreg=0, kreg=1, lreg=2, ipos=3, Delta=12 * Delta_t)
print('mat2 first')
showNonZeroCol(mat2)
mat2 @= intUnij(ireg=1, jreg=1, kreg=1, lreg=2, ipos=3, Delta=8 * Delta_t)
print('mat2 second')
showNonZeroCol(mat2)
# mat @= intUnij(ireg=0, jreg=0, kreg=0, lreg=2, ipos=1, Delta=8 * Delta_t)
# mat @= intUnij(ireg=0, jreg=0, kreg=0, lreg=1, ipos=1, Delta=8 * Delta_t)
# mat = intUDebug2(delta, 100 * lam)

# showNonZero(mat1)

# showNonZero(mat2)

raw list [0, 4, 32, 36, 256, 260, 288, 292]
column list [288, 292, 256, 260, 32, 36, 0, 4]
mat [-1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j]
mat1 first
0
288
[(0.23191526173301824+0j), -0.9720091646891587j]
raw list [0, 1, 2, 3, 4, 5, 6, 7, 32, 33, 34, 35, 36, 37, 38, 39, 256, 257, 258, 259, 260, 261, 262, 263, 288, 289, 290, 291, 292, 293, 294, 295]
column list [288, 289, 290, 291, 292, 293, 294, 295, 256, 257, 258, 259, 260, 261, 262, 263, 32, 33, 34, 35, 36, 37, 38, 39, 0, 1, 2, 3, 4, 5, 6, 7]
mat [-0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259259259259j, -0.9259259

In [174]:
raw_list = [0, 7, 56, 63, 448, 455, 504, 511]
column_list = [504, 511, 448, 455, 56, 63, 0, 7]
nbits = 2 ** (N * M)
Delta = (delta * 100 * 12 * lam) / (96 * (M ** 2))
mat_tmp = np.zeros((nbits, nbits), dtype='complex128')
for i in range(len(raw_list)):
    mat_tmp[raw_list[i]][column_list[i]] = -1j * Delta
print('M, N, delta, lam:', M, N, delta, lam)
print('matrix size:', nbits)
showNonZeroAll(mat_tmp)
expm(mat_tmp)

M, N, delta, lam: 3 3 1 1
matrix size: 512
raw list [0, 7, 56, 63, 448, 455, 504, 511]
column list [504, 511, 448, 455, 56, 63, 0, 7]
mat [-1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j, -1.3888888888888888j]


array([[0.20620676+0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j        ,
        0.        +0.j        , 0.        +0.j  

In [312]:
def commutation(phi1, phi2):
    return phi1 @ phi2 -phi2 @ phi1

In [17]:
# This code shows each phi(i.e. a_n and a_n'^dagger)deos not commute
# M = 5
# count = 0
# comm = commutation(phi(1), phi(2))
# for i in range(phi(1)[0].size):
#     for j in range(phi(1)[0].size):
#         if comm[i][j] != 0:
#             print(comm[i][j])
#             # print(comm[i][j])
#             count += 1
#         if count == 1:
#             break
#     if count == 1:
#         break
# print(count)

In [182]:
M = 2
N_abs = 1
d = 1
N = N_abs * d + d + 1
n = 1
s = math.ceil(math.log2(math.factorial(M)/math.factorial(M - n))) # of ancilla qubits for Bose symm.
tau_0 = 0.5 # Wigner delay
tau_I = 0 # length of time of interaction
delta = 1 # time step
m_0 = 0 # chosen to represent a relevant energy scale in the weak coupling regime
tau = 0
m_t = m_0
lambda_t = 1
a_s = 1

m_ren = m_0
lambda_ren = 1
free_num = int((N_abs + math.log2(n)) * d)
bose_num = int(s + 1)
state = StateZeros(((N * M) + (free_num + bose_num)))
count = 0

while tau <= tau_0 + tau_I:
    # print('count', count)
    # inverse Squeezing operation
    # invS0 = addAncilla(squeezeOpQProd(m_t, a_s), N_abs, n, d, s)
    invS0 = addAncilla(squeezingOp(m_t, a_s), N_abs, n, d, s)
    # invS0 = addAncilla(sqDebug(m_t, a_s), N_abs, n, d, s)
    invS = np.linalg.inv(invS0)
    state = np.dot(invS, state)

    # Change basis
    C = addAncilla(makeGatePerReg(changeBasis(N), M), N_abs, n, d, s)
    state = np.dot(C, state)

    # QFT
    Q = addAncilla(makeGatePerReg(qft(N), M), N_abs, n, d, s)
    state = np.dot(Q, state)

    ## Interaction Hamiltonian
    # # print(lambda_t)
    U_I = addAncilla(intU(delta, lambda_t), N_abs, n, d, s)
    # U_I = addAncilla(intUNProd(delta, lambda_t), N_abs, n, d, s)
    # U_I = addAncilla(intUDebug(delta, 100 * lambda_t), N_abs, n, d, s)
    # U_I = addAncilla(intUDebug2(delta, 100 * lambda_t), N_abs, n, d, s)
    state = np.dot(U_I, state)

    # inverse QFT
    Q = addAncilla(makeGatePerReg(qft(N), M), N_abs, n, d, s)
    invQ = np.linalg.inv(Q)
    state = np.dot(invQ, state)

    # Change basis
    C = addAncilla(makeGatePerReg(changeBasis(N), M), N_abs, n, d, s)
    state = np.dot(C, state)

    # Squeezing operation
    # S = addAncilla(squeezeOpQProd(m_t, a_s), N_abs, n, d, s)
    S = addAncilla(squeezingOp(m_t, a_s), N_abs, n, d, s)
    # S = addAncilla(sqDebug(m_t, a_s), N_abs, n, d, s)
    state = np.dot(S, state)

    count += 1
    print('We count', count, 'steps')

    tau += delta
    if tau < tau_0: # turn on interaction adiabatically
        lambda_t = lambda_ren * (tau / tau_0)
        m_t = m_0 * (1 - (tau / tau_0)) + m_ren * (tau / tau_0)
    elif tau_0 <= tau : # interaction completely
        m_t = m_ren
        lambda_t = lambda_ren

# print(state)

# 結果を保存
result_file = 'calculated_result.pkl'
with open(result_file, 'wb') as f:
    pickle.dump(state, f)

[[ 9.99566035e-01-0.02082731j  0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j
  -4.33964988e-04-0.02082731j  0.00000000e+00+0.j
   0.00000000e+00+0.j          0.00000000e+00+0.j


In [70]:
list = []
for i in range(len(state)):
    if state[i] != 0:
        list.append(state[i])
        print(i)
list

0
36
45
54
63
260
288
325
360
390
432
455
504


[(-0.043786295847682566+0.05881607295685135j),
 (0.3784679668764735-0.31304283968701807j),
 (0.04492923509584299+0.2541934177653032j),
 (-0.12784607756012956-0.045393187832698884j),
 (0.05210956737109052-0.050171237852961056j),
 (0.37849241302396036-0.3130628523860462j),
 (0.3784796452293447-0.31303394873462803j),
 (0.04493204234064055+0.2542097829083181j),
 (0.04492214197906194+0.2541964499233758j),
 (-0.12785428624445308-0.04539614928106796j),
 (-0.12784562381881137-0.045397216576785616j),
 (0.05210956737109051-0.050171237852961056j),
 (0.05210956737109051-0.050171237852961056j)]